In [1]:
try:
    import fastkaggle
except ModuleNotFoundError:
    !pip install -Uq fastkaggle
try:
    import tqdm
except ModuleNotFoundError:
    !pip install tqdm
try:
    import pydicom
except ModuleNotFoundError:
    !pip install pydicom

from fastkaggle import *
from fastai.vision.all import *
from fastai.medical.imaging import *
from fastai.data.all import *
from tqdm.notebook import tqdm
import pydicom

c:\Users\mipbk\anaconda3\envs\myenv\lib\site-packages\torchvision\io\image.py:13: UserWarning: Failed to load image Python extension: [WinError 127] The specified procedure could not be found
  warn(f"Failed to load image Python extension: {e}")


In [3]:
comp = "rsna-pneumonia-detection-challenge"
path = setup_comp(comp, install='fastai "timm>=0.6.2.dev0"')

## Classification & Detection

In [4]:
train_path = path/"stage_2_train_images_subset"
bs = 16
epochs = 1
# arch = 'resnet26d'
arch = 'convnext_tiny_in22k'

In [5]:
labels = pd.read_csv(path/"stage_2_train_labels.csv")
# labels = labels.drop_duplicates("patientId")
labels.head(6)

patientId      x      y  width  height  Target
0  0004cfab-14fd-4e49-80ba-63a80b6bddd6    NaN    NaN    NaN     NaN       0
1  00313ee0-9eaa-42f4-b0ab-c148ed3241cd    NaN    NaN    NaN     NaN       0
2  00322d4d-1c29-4943-afc9-b6754be640eb    NaN    NaN    NaN     NaN       0
3  003d8fa0-6bf1-40ed-b54c-ac657f8495c5    NaN    NaN    NaN     NaN       0
4  00436515-870c-4b36-a041-de91049b9ab4  264.0  152.0  213.0   379.0       1
5  00436515-870c-4b36-a041-de91049b9ab4  562.0  152.0  256.0   453.0       1

In [6]:
def read_dicom_file(fpath):
    dcm = pydicom.read_file(fpath).pixel_array #/ 255
    # dcm = cv2.resize(dcm, (224, 224))#.astype(np.float16)
    img = Image.fromarray(dcm).convert("L")
    return img

In [7]:
def label_func(fname):
    return labels.loc[labels.patientId == fname.name[:-4], "Target"].values[0]

In [8]:
def replace_nan_with_zero(x):
    return np.nan_to_num(x, nan=0)

img2bbox = labels.groupby('patientId').apply(lambda o: (
    replace_nan_with_zero(np.transpose(
        [o['x'], o['y'], o['width'], o['height']])),
    o['Target'].values)).to_dict()


In [9]:
img2bbox["0004cfab-14fd-4e49-80ba-63a80b6bddd6"]

(array([[0., 0., 0., 0.]]), array([0], dtype=int64))

In [10]:
img2bbox["00436515-870c-4b36-a041-de91049b9ab4"]

(array([[264., 152., 213., 379.],
        [562., 152., 256., 453.]]),
 array([1, 1], dtype=int64))

In [11]:
dblock = DataBlock(blocks=(ImageBlock(cls=PILImageBW), BBoxBlock, BBoxLblBlock),
                   n_inp=1,
                   get_items=get_dicom_files,
                   get_x=read_dicom_file,
                   get_y=[lambda o: img2bbox[o.name[:-4]][0],
                          lambda o: img2bbox[o.name[:-4]][1]],
                   splitter=RandomSplitter(),
                   item_tfms=Resize(128),
                   batch_tfms=aug_transforms())

In [12]:
dls = dblock.dataloaders(train_path, bs=bs)

In [13]:
len(dls.train_ds)

218

In [14]:
dls.c=2

In [17]:
dls.show_batch()

RuntimeError: view size is not compatible with input tensor's size and stride (at least one dimension spans across two contiguous subspaces). Use .reshape(...) instead.

In [54]:
from wwf.vision.object_detection import *

In [72]:
# from torchvision.models import resnet34
encoder = create_body(resnet34(), pretrained=True)


In [61]:
arch = RetinaNet(encoder, get_c(dls), final_bias=-4)

In [65]:
ratios = [1/2, 1, 2]
scales = [1, 2**(-1/3), 2**(-2/3)]


In [66]:
crit = RetinaNetFocalLoss(scales=scales, ratios=ratios)

In [ ]:
# https: // www.kaggle.com/code/chenyc15/mean-average-precision-metric/notebook

In [67]:
def _retinanet_split(m): return L(m.encoder, nn.Sequential(
    m.c5top6, m.p6top7, m.merges, m.smoothers, m.classifier, m.box_regressor)).map(params)


In [68]:
learn = Learner(dls, arch, loss_func=crit, splitter=_retinanet_split)


In [69]:
learn.freeze()


In [70]:
learn.fit_one_cycle(10, slice(1e-5, 1e-4))


RuntimeError: view size is not compatible with input tensor's size and stride (at least one dimension spans across two contiguous subspaces). Use .reshape(...) instead.

In [76]:
# learn.fine_tune(epochs=epochs)

In [ ]:
learn.export('model.pkl')

In [ ]:
# learn = load_learner('model.pkl')

In [ ]:
tta_preds, targs = learn.tta(dl=learn.dls.valid)
error_rate(tta_preds, targs)

In [ ]:
interp = ClassificationInterpretation.from_learner(learn)
interp.plot_confusion_matrix()
interp.print_classification_report()

## Submission

Write .csv in following format:

patientId,PredictionString  
0004cfab-14fd-4e49-80ba-63a80b6bddd6,0.5 0 0 100 100  
00313ee0-9eaa-42f4-b0ab-c148ed3241cd,  
00322d4d-1c29-4943-afc9-b6754be640eb,0.8 10 10 50 50 0.75 100 100 5 5

Sort file names

In [ ]:
# import csv

# example data
data = [
    ['0004cfab-14fd-4e49-80ba-63a80b6bddd6', '0.5 0 0 100 100'],
    ['00313ee0-9eaa-42f4-b0ab-c148ed3241cd', ''],
    ['00322d4d-1c29-4943-afc9-b6754be640eb', '0.8 10 10 50 50 0.75 100 100 5 5']
]

# write data to CSV file
with open('predictions.csv', 'w', newline='') as csvfile:
    writer = csv.writer(csvfile)
    writer.writerow(['patientId', 'PredictionString'])
    for row in data:
        writer.writerow(row)

## CAM

## Todos

- sort file name
- use class in training also